In [40]:
import pandas as pd
import numpy as np
from tqdm import tqdm
from sklearn.model_selection import KFold
from sklearn.metrics import classification_report, f1_score
from collections import Counter
import warnings
from pandasgui import show
import gc
import catboost as cb
import ipywidgets
warnings.filterwarnings("ignore")

In [2]:
gc.collect()

20

In [11]:
pd.set_option('display.max_columns',None)
pd.set_option('display.max_rows',1000)

In [47]:
train = pd.read_csv('E:/is_train/is_train_20190702.txt')
ver = pd.read_csv('E:/is_train/is_train_20190701.txt')
#test = pd.read_csv('is_test_2.txt')

In [172]:
temp = train.sort_values(by='future_slice_id')

In [139]:
temp[0:574]

link  label  current_slice_id  future_slice_id  time_diff  \
16106   508561      0               -16                0         16   
61421   221504      0               -29                0         29   
61415   613405      0               -20                0         20   
428545  578266      0               -28                0         28   
400653  326141      0               -26                0         26   
83317   203546      0               -20                0         20   
120522  141551      0                -1                0          1   
96315   275693      0                -8                0          8   
33210    34035      0               -13                0         13   
486223  182302      0               -21                0         21   
114573  655052      0                -5                0          5   
219325  310290      0               -11                0         11   
495115  170649      0               -10                0         10   
448184  679054      0                -6                0          6   
290402   79111      0               -24                0         24   
18094   507814      0               -20                0         20   
237466  219946      0                -9                0          9   
110505   56233      0               -24                0         24   
385520  223676      0                -4                0          4   
188929  448646      0               -11                0         11   
469353  271204      0                -1                0          1   
96586   193313      0                -3                0          3   
96641   276254      0               -13                0         13   
268708   98984      0               -23                0         23   
456294    8091      0               -20                0         20   
373649  272980      0               -15                0         15   
18811    99505      0               -13                0         13   
391655  505627      0               -13                0         13   
333736  382693      0               -11                0         11   
174390  182878      0                -5                0          5   
159970  335841      0               -16                0         16   
189089    3869      0               -26                0         26   
61801   179822      0               -29                0         29   
373593  221504      0               -26                0         26   
253305  379676      0               -13                0         13   
359146  240958      0               -19                0         19   
32741   379676      0               -14                0         14   
83103   276254      0                -4                0          4   
486281  576960      0                -2                0          2   
32880   193362      0               -15                0         15   
61489    60892      0               -23                0         23   
333719  137209      0               -23                0         23   
447629   39757      0               -29                0         29   
420013  613405      0               -18                0         18   
455534  232908      0               -14                0         14   
219651    8091      0               -29                0         29   
105715  221504      0               -25                0         25   
34007   214147      0               -15                0         15   
159143  508655      0               -25                0         25   
392070  272980      0                -9                0          9   
289842  118207      0                -9                0          9   
59635   424020      0               -14                0         14   
127457  249799      0               -10                0         10   
391994   70664      0               -11                0         11   
177943  186776      0                -9                0          9   
315596  270765      0             

In [177]:
ahh = (temp.groupby(['future_slice_id','label']).count()).copy()

In [178]:
ahh[0:10]

link  current_slice_id  time_diff  now_speed  now_eta  \
future_slice_id label                                                          
0               0       573               573        573        573      573   
1               0       552               552        552        552      552   
                1        12                12         12         12       12   
                2         3                 3          3          3        3   
2               0       552               552        552        552      552   
                1         9                 9          9          9        9   
                2         6                 6          6          6        6   
3               0       516               516        516        516      516   
                1         9                 9          9          9        9   
4               0       510               510        510        510      510   

                       now_cnt  now_state  current_speed_min  \
future_slice_id label                                          
0               0          573        573                573   
1               0          552        552                552   
                1           12         12                 12   
                2            3          3                  3   
2               0          552        552                552   
                1            9          9                  9   
                2            6          6                  6   
3               0          516        516                516   
                1            9          9                  9   
4               0          510        510                510   

                       current_speed_max  current_speed_mean  \
future_slice_id label                                          
0               0                    573                 573   
1               0                    552                 552   
                1                     12                  12   
                2                      3                   3   
2               0                    552                 552   
                1                      9                   9   
                2                      6                   6   
3               0                    516                 516   
                1                      9                   9   
4               0                    510                 510   

                       current_speed_std  current_eta_min  current_eta_max  \
future_slice_id label                                                        
0               0                    573              573              573   
1               0                    552              552              552   
                1                     12               12               12   
                2                      3                3                3   
2               0                    552              552              552   
                1                      9                9                9   
                2                      6                6                6   
3               0                    516              516              516   
                1                      9                9                9   
4               0                    510              510              510   

                       current_eta_mean  current_eta_std  current_cnt_min  \
future_slice_id label                                                       
0               0                   573              573              573   
1               0                   552              552              552   
                1                    12               12               12   
                2                     3                3                3   
2               0                   552              552              552   
                1                     9         

In [179]:
#a1 = temp.groupby(['future_slice_id','label'])
a1['future_slice_id'].sum()[2].values

array([1104,   18,   12], dtype=int64)

In [163]:
#a1 = temp.groupby(['future_slice_id','label'])
sum_ = []
for i in range(720):
    temp = a1['future_slice_id'].sum()[i].values
    lenth = len(temp)
    print(temp)
    a = []
    if(lenth==3):
        a.append(temp[0])
        a.append(temp[1])
        a.append(temp[2])
    if(lenth==2):
        a.append(temp[0])
        a.append(temp[1])
        a.append(0)
    if(lenth==1):
        a.append(temp[0])
        a.append(0)
        a.append(0)
    #print(lenth) 
    sum_.append(a)

[0]
[552  12   3]
[1104   18   12]
[1548   27]
[2040   60   12]
[2655   90   30]
[3258  144   18]
[3780   42]
[4392   48]
[5292  108]
[4980   90]
[5742   99   33]
[6120   36   36]
[5733   39]
[7056  126   42]
[7830  225]
[9168  240   48]
[9180  255  102]
[8208  216   54]
[11514   171]
[9240  120  120]
[11844   126    63]
[10758    66]
[10074   138]
[12312   144   144]
[11850   150   150]
[12012    78    78]
[11664    81    81]
[13776    84]
[13137   174]
[15570    90   180]
[13857   279]
[14016    96]
[15543    99    99]
[15912   204]
[13545   210   105]
[15012   540]
[16761   333   111]
[18354   114   228]
[14508   468]
[17520   360   120]
[15744   123]
[15372   126]
[19608   516   258]
[20328   396   264]
[17010   540   270]
[19182   276   138]
[18471   282   423]
[17856   288]
[19992   588   147]
[18900   300   300]
[20655   306]
[23244   156]
[18762]
[18468   324]
[21615   495]
[21840   168]
[20349   684]
[23838   174]
[24780   531]
[20880   720   180]
[24156   183]
[21762   558]
[

[309120  38976   8064]
[309810  60615   9429]
[328050  62100  12150]
[305778  66297   6765]
[326796  69156  18984]
[354699  58437   8154]
[321432  50394  10896]
[363090  75075   9555]
[324216  53352   8208]
[298878  42501   2742]
[321516  56334  19236]
[337365  56457   8262]
[316020  42780   9660]
[320856  51171  15213]
[336798  60984   8316]
[291690  54171  12501]
[296496  65424  12528]
[376650  57195   4185]
[342510  74094   8388]
[326433  57441  11208]
[334152  54756   9828]
[320796  56280  11256]
[301740  62040  12690]
[334881  55107  24021]
[293112  60888  24072]
[329208  56760  21285]
[328482  75366  15642]
[353400  65550  17100]
[331296  58548  17136]
[343440  65826   7155]
[347028  64530   8604]
[294585  44547  12933]
[351360  63360  10080]
[317460  57720  20202]
[361500  53502  11568]
[352107  63756  11592]
[281688  62436  18876]
[296820  61110  26190]
[341172  64152  16038]
[376938  49674   5844]
[339648  52704  20496]
[337410  52812  16137]
[336630  69090  13230]
[319641  51

In [3]:
train['is_night'] = train['future_slice_id'].apply(lambda x: 0 if (0< x <= 172) | (x>=690) else 1)
ver['is_night'] = ver['future_slice_id'].apply(lambda x: 0 if (0< x <= 172) | (x>=690) else 1)
test['is_night'] = test['future_slice_id'].apply(lambda x: 0 if (0< x <= 172) | (x>=690) else 1)

In [48]:
attr = pd.read_csv('attr.txt', sep='\t',
                       names=['link', 'length', 'direction', 'path_class', 'speed_class', 'LaneNum', 'speed_limit',
                              'level', 'width'], header=None)

In [50]:
train = train.merge(attr, on='link', how='left')
ver = ver.merge(attr, on='link', how='left')
#test = test.merge(attr, on='link', how='left')

In [58]:
cor = ['now_state','current_state_zhong','current_state_max', 'current_state_min', 'his_28_state_zhong', 'his_28_state_max', 'his_28_state_min',
  'his_21_state_zhong','his_21_state_max', 'his_21_state_min',  'his_14_state_zhong', 'his_14_state_max', 'his_14_state_min','his_7_state_zhong', 'his_7_state_max','his_7_state_min',]

In [51]:
pro = pd.read_csv('per_road_pro.txt')

In [52]:
train = train.merge(pro, on='link', how='left')
ver = ver.merge(pro, on='link', how='left')
#test = test.merge(pro, on='link', how='left')

In [53]:
use_cols = [i for i in train.columns if i not in ['link', 'label']]
#use_cols = [i for i in train.columns if i not in ['link', 'label', 'current_state_min' ,'his_28_state_min','his_21_state_min', 'his_14_state_min','his_7_state_min']]

In [54]:
X_train= (train.loc[:,use_cols])
y_train = (train['label'])
X_ver= (ver.loc[:,use_cols])
y_ver = (ver['label'])
#X_test= (test.loc[:,use_cols])

In [55]:
folds = KFold(n_splits=5, shuffle=True, random_state=2020)
train_user_id = train['link'].unique()

In [41]:
model = cb.CatBoostClassifier(iterations=200,depth=8,l2_leaf_reg=8,learning_rate=0.5,random_strength=1,loss_function='MultiClassOneVsAll',logging_level='Verbose')
#    model.fit(train_x,train_y,eval_set=(valid_x,valid_y),sample_weight=w,early_stopping_rounds=20)

In [100]:
class AccuracyMetric(object):

    def get_final_error(self, error, weight):
        #print(error,weight)
        return error
    
    def is_max_optimal(self):
        return True

    def evaluate(self, approxes, target, weight):
        #预测标签
        best_class = np.argmax(approxes, axis=0)
        weight_sum = 0 
        
        report = f1_score(np.array(target).reshape(-1), best_class.reshape(-1),average=None)
        res = report[0] * 0.2 + report[1] * 0.2 + report[2] * 0.6
        #print(res)

        for i in range(len(target)):
            w = 1.0 if weight is None else weight[i]
            weight_sum += w

        return res, weight_sum

In [104]:
w = np.array((y_train+1))
model = cb.CatBoostClassifier(iterations=200,depth=6,l2_leaf_reg=8,learning_rate=0.5,random_strength=1,eval_metric=AccuracyMetric(),loss_function='MultiClassOneVsAll',logging_level='Verbose')
model.fit(X_train,y_train,eval_set=(X_ver,y_ver),sample_weight=w,early_stopping_rounds=20)
pred_res = model.predict(X_ver)
print(classification_report(y_ver,pred_res, digits=4))
report = f1_score(y_ver,pred_res, average=None)
print('Score: ', report[0] * 0.2 + report[1] * 0.2 + report[2] * 0.6)

0:	learn: 0.5162002	test: 0.5212097	best: 0.5212097 (0)	total: 2.21s	remaining: 7m 19s
1:	learn: 0.5560073	test: 0.5558512	best: 0.5558512 (1)	total: 4.42s	remaining: 7m 17s
2:	learn: 0.5649682	test: 0.5624447	best: 0.5624447 (2)	total: 6.64s	remaining: 7m 16s
3:	learn: 0.5754109	test: 0.5725404	best: 0.5725404 (3)	total: 8.9s	remaining: 7m 15s
4:	learn: 0.5828189	test: 0.5842955	best: 0.5842955 (4)	total: 11.1s	remaining: 7m 11s
5:	learn: 0.5891686	test: 0.5890674	best: 0.5890674 (5)	total: 13.4s	remaining: 7m 13s
6:	learn: 0.5913044	test: 0.5916725	best: 0.5916725 (6)	total: 15.6s	remaining: 7m 11s
7:	learn: 0.5942578	test: 0.5937226	best: 0.5937226 (7)	total: 17.8s	remaining: 7m 7s
8:	learn: 0.5954585	test: 0.5940325	best: 0.5940325 (8)	total: 20.1s	remaining: 7m 7s
9:	learn: 0.5965863	test: 0.5958429	best: 0.5958429 (9)	total: 22.4s	remaining: 7m 6s
10:	learn: 0.5977533	test: 0.5975390	best: 0.5975390 (10)	total: 24.6s	remaining: 7m 1s
11:	learn: 0.5986524	test: 0.5974329	best: 0.5

In [106]:
w = np.array((y_train+1))
model = cb.CatBoostClassifier(iterations=200,depth=6,l2_leaf_reg=8,learning_rate=0.5,random_strength=1,loss_function='MultiClassOneVsAll',logging_level='Verbose')
model.fit(X_train,y_train,eval_set=(X_ver,y_ver),sample_weight=w,early_stopping_rounds=20)
pred_res = model.predict(X_ver)
print(classification_report(y_ver,pred_res, digits=4))
report = f1_score(y_ver,pred_res, average=None)
print('Score: ', report[0] * 0.2 + report[1] * 0.2 + report[2] * 0.6)

0:	learn: 0.4707983	test: 0.4343277	best: 0.4343277 (0)	total: 415ms	remaining: 1m 22s
1:	learn: 0.3845757	test: 0.3327867	best: 0.3327867 (1)	total: 895ms	remaining: 1m 28s
2:	learn: 0.3447130	test: 0.2837648	best: 0.2837648 (2)	total: 1.31s	remaining: 1m 26s
3:	learn: 0.3240948	test: 0.2578618	best: 0.2578618 (3)	total: 1.74s	remaining: 1m 25s
4:	learn: 0.3123453	test: 0.2438271	best: 0.2438271 (4)	total: 2.13s	remaining: 1m 22s
5:	learn: 0.3050955	test: 0.2347090	best: 0.2347090 (5)	total: 2.54s	remaining: 1m 22s
6:	learn: 0.2997999	test: 0.2292853	best: 0.2292853 (6)	total: 2.95s	remaining: 1m 21s
7:	learn: 0.2977902	test: 0.2264508	best: 0.2264508 (7)	total: 3.33s	remaining: 1m 19s
8:	learn: 0.2949878	test: 0.2240696	best: 0.2240696 (8)	total: 3.85s	remaining: 1m 21s
9:	learn: 0.2933150	test: 0.2226369	best: 0.2226369 (9)	total: 4.47s	remaining: 1m 24s
10:	learn: 0.2922816	test: 0.2218976	best: 0.2218976 (10)	total: 4.86s	remaining: 1m 23s
11:	learn: 0.2916111	test: 0.2212884	best

In [98]:
id_col = 'link'
use_train_feats = use_cols
label = 'label'
pred = np.zeros((len(X_ver),3))
train_pred = np.zeros((len(X_train),3))
categorical_features_indices = np.where(X_train.dtypes != np.float)[0]
for n_fold, (train_idx, valid_idx) in enumerate(folds.split(train_user_id), start=1):
    print('the {} training start ...'.format(n_fold))
    train_x, train_y = train.loc[train[id_col].isin(train_user_id[train_idx]), use_train_feats], train.loc[
            train[id_col].isin(train_user_id[train_idx]), label]
    #print(train_y.shape)#405900
    valid_x, valid_y = train.loc[train[id_col].isin(train_user_id[valid_idx]), use_train_feats], train.loc[
            train[id_col].isin(train_user_id[valid_idx]), label]
    w = np.array((train_y+1))
    model = cb.CatBoostClassifier(iterations=200,depth=8,l2_leaf_reg=8,learning_rate=0.5,random_strength=1,eval_metric=AccuracyMetric(),loss_function='MultiClassOneVsAll',logging_level='Verbose')
    model.fit(train_x,train_y,eval_set=(valid_x,valid_y),sample_weight=w,early_stopping_rounds=20)
    #model.fit(train_x,train_y,eval_set=(valid_x,valid_y),early_stopping_rounds=20)
    train_pred += model.predict_proba(X_train)/n_fold
    pred += model.predict_proba(X_ver)/n_fold
pred_res = np.argmax(pred,axis=1)
train_res = np.argmax(train_pred,axis=1)
print(classification_report(y_ver,pred_res, digits=4))
report = f1_score(y_ver,pred_res, average=None)
print('Score: ', report[0] * 0.2 + report[1] * 0.2 + report[2] * 0.6)

the 1 training start ...
0.5320977900595772
0.5320977900595772 492780.0
0.5587352245907831
0.5587352245907831 100053.0
0:	learn: 0.5320978	test: 0.5587352	best: 0.5587352 (0)	total: 2.13s	remaining: 7m 5s
0.5630457825475907
0.5630457825475907 492780.0
0.5779338082666017
0.5779338082666017 100053.0
1:	learn: 0.5630458	test: 0.5779338	best: 0.5779338 (1)	total: 4.26s	remaining: 7m 1s
0.5730633012144806
0.5730633012144806 492780.0
0.5831514891524516
0.5831514891524516 100053.0
2:	learn: 0.5730633	test: 0.5831515	best: 0.5831515 (2)	total: 6.39s	remaining: 6m 59s
0.5813096174052342
0.5813096174052342 492780.0
0.5958142549490382
0.5958142549490382 100053.0
3:	learn: 0.5813096	test: 0.5958143	best: 0.5958143 (3)	total: 8.56s	remaining: 6m 59s
0.5837065335345875
0.5837065335345875 492780.0
0.601027617352575
0.601027617352575 100053.0
4:	learn: 0.5837065	test: 0.6010276	best: 0.6010276 (4)	total: 10.7s	remaining: 6m 58s
0.5879056134678536
0.5879056134678536 492780.0
0.6020628461962856
0.602062

0.5825971262748295 100860.0
7:	learn: 0.6041846	test: 0.5825971	best: 0.5825971 (7)	total: 16.4s	remaining: 6m 32s
0.6073934158285575
0.6073934158285575 492342.0
0.5829169225592509
0.5829169225592509 100860.0
8:	learn: 0.6073934	test: 0.5829169	best: 0.5829169 (8)	total: 18.5s	remaining: 6m 31s
0.6088897148116943
0.6088897148116943 492342.0
0.5818477690854824
0.5818477690854824 100860.0
9:	learn: 0.6088897	test: 0.5818478	best: 0.5829169 (8)	total: 20.5s	remaining: 6m 29s
0.610083066889328
0.610083066889328 492342.0
0.5847281252376109
0.5847281252376109 100860.0
10:	learn: 0.6100831	test: 0.5847281	best: 0.5847281 (10)	total: 22.5s	remaining: 6m 27s
0.6124269394864584
0.6124269394864584 492342.0
0.5866909633857649
0.5866909633857649 100860.0
11:	learn: 0.6124269	test: 0.5866910	best: 0.5866910 (11)	total: 24.5s	remaining: 6m 24s
0.6137053560041121
0.6137053560041121 492342.0
0.5866921605321234
0.5866921605321234 100860.0
12:	learn: 0.6137054	test: 0.5866922	best: 0.5866922 (12)	total: 

0.6222293875628984
0.6222293875628984 491457.0
0.5935321024105482
0.5935321024105482 101388.0
16:	learn: 0.6222294	test: 0.5935321	best: 0.5977913 (12)	total: 36.4s	remaining: 6m 31s
0.625303545715151
0.625303545715151 491457.0
0.5943194159099467
0.5943194159099467 101388.0
17:	learn: 0.6253035	test: 0.5943194	best: 0.5977913 (12)	total: 38.3s	remaining: 6m 27s
0.6268294068154739
0.6268294068154739 491457.0
0.5936713808023364
0.5936713808023364 101388.0
18:	learn: 0.6268294	test: 0.5936714	best: 0.5977913 (12)	total: 40.5s	remaining: 6m 25s
0.6294624478810034
0.6294624478810034 491457.0
0.5956089301511482
0.5956089301511482 101388.0
19:	learn: 0.6294624	test: 0.5956089	best: 0.5977913 (12)	total: 42.5s	remaining: 6m 22s
0.6313146660141
0.6313146660141 491457.0
0.595944122857581
0.595944122857581 101388.0
20:	learn: 0.6313147	test: 0.5959441	best: 0.5977913 (12)	total: 44.5s	remaining: 6m 19s
0.6337141095226377
0.6337141095226377 491457.0
0.5948618943811419
0.5948618943811419 101388.0
2

0.5999519379186908 101469.0
27:	learn: 0.6377510	test: 0.5999519	best: 0.6026670 (18)	total: 59.3s	remaining: 6m 4s
0.6383257152405278
0.6383257152405278 491769.0
0.6014438593242784
0.6014438593242784 101469.0
28:	learn: 0.6383257	test: 0.6014439	best: 0.6026670 (18)	total: 1m 1s	remaining: 6m 2s
0.6414454394410907
0.6414454394410907 491769.0
0.5992846992683163
0.5992846992683163 101469.0
29:	learn: 0.6414454	test: 0.5992847	best: 0.6026670 (18)	total: 1m 3s	remaining: 6m 1s
0.6425121600505752
0.6425121600505752 491769.0
0.60044354223569
0.60044354223569 101469.0
30:	learn: 0.6425122	test: 0.6004435	best: 0.6026670 (18)	total: 1m 6s	remaining: 6m
0.643228205604308
0.643228205604308 491769.0
0.5990925306860562
0.5990925306860562 101469.0
31:	learn: 0.6432282	test: 0.5990925	best: 0.6026670 (18)	total: 1m 8s	remaining: 5m 57s
0.6472790256127285
0.6472790256127285 491769.0
0.6026790455874987
0.6026790455874987 101469.0
32:	learn: 0.6472790	test: 0.6026790	best: 0.6026790 (32)	total: 1m 10

0.627750922962403
0.627750922962403 490788.0
0.5755158084971576
0.5755158084971576 102183.0
19:	learn: 0.6277509	test: 0.5755158	best: 0.5803198 (16)	total: 40.8s	remaining: 6m 6s
0.629724483394269
0.629724483394269 490788.0
0.577658250897709
0.577658250897709 102183.0
20:	learn: 0.6297245	test: 0.5776583	best: 0.5803198 (16)	total: 43s	remaining: 6m 6s
0.6318821720150252
0.6318821720150252 490788.0
0.578962942613551
0.578962942613551 102183.0
21:	learn: 0.6318822	test: 0.5789629	best: 0.5803198 (16)	total: 45.2s	remaining: 6m 5s
0.6332828894339342
0.6332828894339342 490788.0
0.5800735822932932
0.5800735822932932 102183.0
22:	learn: 0.6332829	test: 0.5800736	best: 0.5803198 (16)	total: 47.4s	remaining: 6m 4s
0.6342793388385604
0.6342793388385604 490788.0
0.5802548308895452
0.5802548308895452 102183.0
23:	learn: 0.6342793	test: 0.5802548	best: 0.5803198 (16)	total: 49.4s	remaining: 6m 1s
0.635138985156815
0.635138985156815 490788.0
0.5804095247588739
0.5804095247588739 102183.0
24:	lear

In [99]:
id_col = 'link'
use_train_feats = use_cols
label = 'label'
pred = np.zeros((len(X_ver),3))
train_pred = np.zeros((len(X_train),3))
categorical_features_indices = np.where(X_train.dtypes != np.float)[0]
for n_fold, (train_idx, valid_idx) in enumerate(folds.split(train_user_id), start=1):
    print('the {} training start ...'.format(n_fold))
    train_x, train_y = train.loc[train[id_col].isin(train_user_id[train_idx]), use_train_feats], train.loc[
            train[id_col].isin(train_user_id[train_idx]), label]
    #print(train_y.shape)#405900
    valid_x, valid_y = train.loc[train[id_col].isin(train_user_id[valid_idx]), use_train_feats], train.loc[
            train[id_col].isin(train_user_id[valid_idx]), label]
    w = np.array((train_y+1))
    model = cb.CatBoostClassifier(iterations=200,depth=8,l2_leaf_reg=8,learning_rate=0.5,random_strength=1,loss_function='MultiClassOneVsAll',logging_level='Verbose')
    model.fit(train_x,train_y,eval_set=(valid_x,valid_y),sample_weight=w,early_stopping_rounds=20)
    #model.fit(train_x,train_y,eval_set=(valid_x,valid_y),early_stopping_rounds=20)
    train_pred += model.predict_proba(X_train)/n_fold
    pred += model.predict_proba(X_ver)/n_fold
pred_res = np.argmax(pred,axis=1)
train_res = np.argmax(train_pred,axis=1)
print(classification_report(y_ver,pred_res, digits=4))
report = f1_score(y_ver,pred_res, average=None)
print('Score: ', report[0] * 0.2 + report[1] * 0.2 + report[2] * 0.6)

the 1 training start ...
0:	learn: 0.4655869	test: 0.4334814	best: 0.4334814 (0)	total: 1.3s	remaining: 4m 18s
1:	learn: 0.3796401	test: 0.3335466	best: 0.3335466 (1)	total: 2.49s	remaining: 4m 6s
2:	learn: 0.3398333	test: 0.2858339	best: 0.2858339 (2)	total: 3.68s	remaining: 4m 1s
3:	learn: 0.3176067	test: 0.2588779	best: 0.2588779 (3)	total: 4.91s	remaining: 4m
4:	learn: 0.3059694	test: 0.2444112	best: 0.2444112 (4)	total: 6.13s	remaining: 3m 59s
5:	learn: 0.2996640	test: 0.2365492	best: 0.2365492 (5)	total: 7.31s	remaining: 3m 56s
6:	learn: 0.2956461	test: 0.2320628	best: 0.2320628 (6)	total: 8.47s	remaining: 3m 53s
7:	learn: 0.2930043	test: 0.2294529	best: 0.2294529 (7)	total: 9.79s	remaining: 3m 55s
8:	learn: 0.2907416	test: 0.2273488	best: 0.2273488 (8)	total: 11.3s	remaining: 3m 59s
9:	learn: 0.2891101	test: 0.2261385	best: 0.2261385 (9)	total: 12.5s	remaining: 3m 56s
10:	learn: 0.2881468	test: 0.2255833	best: 0.2255833 (10)	total: 13.7s	remaining: 3m 54s
11:	learn: 0.2868920	te

46:	learn: 0.2611578	test: 0.2219115	best: 0.2215152 (33)	total: 58.8s	remaining: 3m 11s
47:	learn: 0.2607305	test: 0.2219620	best: 0.2215152 (33)	total: 59.9s	remaining: 3m 9s
48:	learn: 0.2600615	test: 0.2220627	best: 0.2215152 (33)	total: 1m 1s	remaining: 3m 8s
49:	learn: 0.2593690	test: 0.2221711	best: 0.2215152 (33)	total: 1m 2s	remaining: 3m 6s
50:	learn: 0.2589224	test: 0.2221504	best: 0.2215152 (33)	total: 1m 3s	remaining: 3m 5s
51:	learn: 0.2581910	test: 0.2223220	best: 0.2215152 (33)	total: 1m 4s	remaining: 3m 3s
52:	learn: 0.2577192	test: 0.2224696	best: 0.2215152 (33)	total: 1m 5s	remaining: 3m 1s
53:	learn: 0.2568412	test: 0.2223865	best: 0.2215152 (33)	total: 1m 6s	remaining: 3m
Stopped by overfitting detector  (20 iterations wait)

bestTest = 0.2215151953
bestIteration = 33

Shrink model to first 34 iterations.
the 3 training start ...
0:	learn: 0.4648349	test: 0.4347602	best: 0.4347602 (0)	total: 1.19s	remaining: 3m 56s
1:	learn: 0.3786611	test: 0.3353329	best: 0.335332

1:	learn: 0.3812457	test: 0.3301889	best: 0.3301889 (1)	total: 2.3s	remaining: 3m 47s
2:	learn: 0.3408160	test: 0.2803763	best: 0.2803763 (2)	total: 3.41s	remaining: 3m 44s
3:	learn: 0.3197150	test: 0.2540683	best: 0.2540683 (3)	total: 4.54s	remaining: 3m 42s
4:	learn: 0.3074738	test: 0.2388499	best: 0.2388499 (4)	total: 5.68s	remaining: 3m 41s
5:	learn: 0.3017033	test: 0.2307251	best: 0.2307251 (5)	total: 6.82s	remaining: 3m 40s
6:	learn: 0.2984089	test: 0.2264685	best: 0.2264685 (6)	total: 7.93s	remaining: 3m 38s
7:	learn: 0.2949877	test: 0.2231042	best: 0.2231042 (7)	total: 9.05s	remaining: 3m 37s
8:	learn: 0.2923637	test: 0.2211561	best: 0.2211561 (8)	total: 10.2s	remaining: 3m 35s
9:	learn: 0.2906236	test: 0.2199447	best: 0.2199447 (9)	total: 11.4s	remaining: 3m 35s
10:	learn: 0.2896456	test: 0.2193666	best: 0.2193666 (10)	total: 12.5s	remaining: 3m 34s
11:	learn: 0.2884926	test: 0.2189484	best: 0.2189484 (11)	total: 13.6s	remaining: 3m 33s
12:	learn: 0.2870871	test: 0.2184964	bes

40:	learn: 0.2660208	test: 0.2198708	best: 0.2197480 (39)	total: 51.9s	remaining: 3m 21s
41:	learn: 0.2655027	test: 0.2198771	best: 0.2197480 (39)	total: 53.2s	remaining: 3m 20s
42:	learn: 0.2648307	test: 0.2198329	best: 0.2197480 (39)	total: 54.6s	remaining: 3m 19s
43:	learn: 0.2645051	test: 0.2198696	best: 0.2197480 (39)	total: 55.9s	remaining: 3m 18s
44:	learn: 0.2638628	test: 0.2198779	best: 0.2197480 (39)	total: 57.1s	remaining: 3m 16s
45:	learn: 0.2632857	test: 0.2198545	best: 0.2197480 (39)	total: 58.3s	remaining: 3m 15s
46:	learn: 0.2628116	test: 0.2198453	best: 0.2197480 (39)	total: 59.4s	remaining: 3m 13s
47:	learn: 0.2620667	test: 0.2199442	best: 0.2197480 (39)	total: 1m	remaining: 3m 11s
48:	learn: 0.2613585	test: 0.2198683	best: 0.2197480 (39)	total: 1m 1s	remaining: 3m 10s
49:	learn: 0.2607152	test: 0.2198784	best: 0.2197480 (39)	total: 1m 2s	remaining: 3m 8s
50:	learn: 0.2599925	test: 0.2200556	best: 0.2197480 (39)	total: 1m 3s	remaining: 3m 6s
51:	learn: 0.2595022	test:

In [ ]:
print(classification_report(y_train,pred_res, digits=4))
report = f1_score(y_ver,pred_res, average=None)
print('Score: ', report[0] * 0.2 + report[1] * 0.2 + report[2] * 0.6)

In [157]:
ver['pred_res'] = pred.reshape(-1)

In [151]:
train_res = model.predict(X_train)
report = f1_score(y_train,train_res, average=None)
print('Score: ', report[0] * 0.2 + report[1] * 0.2 + report[2] * 0.6)

Score:  0.6576306885983174


In [124]:
model = cb.CatBoostClassifier(iterations=200,loss_function='MultiClassOneVsAll',logging_level='Verbose')
grid = {'depth': [4, 6, 10],
        'l2_leaf_reg': [1, 3, 5, 7, 9]}
grid_search_result = model.grid_search(grid, 
                                       X=X_train, 
                                       y=y_train, 
                                       plot=True)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))


bestTest = 0.20964483
bestIteration = 199

0:	loss: 0.2096448	best: 0.2096448 (0)	total: 1m 25s	remaining: 19m 50s

bestTest = 0.20967359
bestIteration = 199

1:	loss: 0.2096736	best: 0.2096448 (0)	total: 2m 37s	remaining: 17m 5s

bestTest = 0.2097019887
bestIteration = 199

2:	loss: 0.2097020	best: 0.2096448 (0)	total: 3m 44s	remaining: 14m 59s

bestTest = 0.2097080456
bestIteration = 199

3:	loss: 0.2097080	best: 0.2096448 (0)	total: 4m 47s	remaining: 13m 11s

bestTest = 0.2097379964
bestIteration = 199

4:	loss: 0.2097380	best: 0.2096448 (0)	total: 5m 55s	remaining: 11m 50s

bestTest = 0.2066388147
bestIteration = 199

5:	loss: 0.2066388	best: 0.2066388 (5)	total: 7m 27s	remaining: 11m 10s

bestTest = 0.2066662177
bestIteration = 199

6:	loss: 0.2066662	best: 0.2066388 (5)	total: 8m 59s	remaining: 10m 16s

bestTest = 0.2066382217
bestIteration = 199

7:	loss: 0.2066382	best: 0.2066382 (7)	total: 10m 29s	remaining: 9m 11s

bestTest = 0.2067952013
bestIteration = 199

8:	loss: 0.2067

KeyboardInterrupt: 

In [32]:
temp = test[['link', 'current_slice_id', 'future_slice_id', 'label']]
temp['label']=pred_res+1

In [33]:
temp.to_csv('2020_11_15.csv', index=False, encoding='utf8')

In [212]:
print(classification_report(y_train,train_res, digits=4))
report = f1_score(y_train,train_res, average=None)
print('Score: ', report[0] * 0.2 + report[1] * 0.2 + report[2] * 0.6)

              precision    recall  f1-score   support

           0     0.9393    0.9148    0.9269    415227
           1     0.5643    0.6476    0.6031     72621
           2     0.5464    0.5504    0.5484     18105

    accuracy                         0.8634    505953
   macro avg     0.6834    0.7042    0.6928    505953
weighted avg     0.8714    0.8634    0.8669    505953

Score:  0.6350452674366583


In [2]:
import matplotlib.pyplot as plt 
fea_ = model.feature_importances_
fea_name = model.feature_names_
plt.figure(figsize=(10, 40))
plt.barh(fea_name,fea_,height =0.5)
plt.show()

NameError: name 'model' is not defined

In [21]:
from sklearn.ensemble import BaggingClassifier
tree = cb.CatBoostClassifier(iterations=100,depth=6,l2_leaf_reg=8,learning_rate=0.5,random_strength=1,loss_function='MultiClassOneVsAll',logging_level='Verbose')
bag = BaggingClassifier(base_estimator=tree,n_estimators=4,max_samples=1.0,max_features=1.0,bootstrap=True,
                        bootstrap_features=False,n_jobs=1,random_state=1)
from sklearn.metrics import accuracy_score
w = np.array(y_ver)
w = np.where(w==0,1.25,w)
w = np.where(w==1,1.85,w)
w = np.where(w==2,2.9,w)
bag = bag.fit(X_ver,y_ver,sample_weight=w)
y_train_pred = bag.predict(X_train)
y_test_pred = bag.predict(X_ver)
bag_train = accuracy_score(y_train,y_train_pred)
bag_test = accuracy_score(y_ver,y_test_pred)
print('Bagging train/test accuracies %.3f/%.3f' % (bag_train,bag_test))

0:	learn: 0.4361755	total: 689ms	remaining: 1m 8s
1:	learn: 0.3398281	total: 1.22s	remaining: 59.7s
2:	learn: 0.2944264	total: 1.83s	remaining: 59.1s
3:	learn: 0.2712278	total: 2.42s	remaining: 58.2s
4:	learn: 0.2581880	total: 2.97s	remaining: 56.4s
5:	learn: 0.2505719	total: 3.54s	remaining: 55.5s
6:	learn: 0.2460911	total: 4.09s	remaining: 54.4s
7:	learn: 0.2432186	total: 4.63s	remaining: 53.3s
8:	learn: 0.2411569	total: 5.29s	remaining: 53.4s
9:	learn: 0.2399191	total: 5.92s	remaining: 53.3s
10:	learn: 0.2386962	total: 6.58s	remaining: 53.3s
11:	learn: 0.2381040	total: 7.25s	remaining: 53.1s
12:	learn: 0.2376405	total: 7.88s	remaining: 52.7s
13:	learn: 0.2369806	total: 8.51s	remaining: 52.3s
14:	learn: 0.2357723	total: 9.16s	remaining: 51.9s
15:	learn: 0.2352761	total: 9.72s	remaining: 51.1s
16:	learn: 0.2349138	total: 10.2s	remaining: 50s
17:	learn: 0.2339886	total: 11s	remaining: 50.1s
18:	learn: 0.2333592	total: 11.5s	remaining: 49.2s
19:	learn: 0.2329800	total: 12.1s	remaining: 

62:	learn: 0.2206760	total: 59.9s	remaining: 35.2s
63:	learn: 0.2204898	total: 1m	remaining: 34.1s
64:	learn: 0.2202396	total: 1m 1s	remaining: 33.1s
65:	learn: 0.2198582	total: 1m 2s	remaining: 32.3s
66:	learn: 0.2196021	total: 1m 3s	remaining: 31.4s
67:	learn: 0.2193812	total: 1m 4s	remaining: 30.3s
68:	learn: 0.2190846	total: 1m 5s	remaining: 29.3s
69:	learn: 0.2188989	total: 1m 5s	remaining: 28.2s
70:	learn: 0.2186372	total: 1m 6s	remaining: 27.2s
71:	learn: 0.2184721	total: 1m 7s	remaining: 26.1s
72:	learn: 0.2183457	total: 1m 7s	remaining: 25.1s
73:	learn: 0.2181584	total: 1m 8s	remaining: 24.1s
74:	learn: 0.2179281	total: 1m 9s	remaining: 23.2s
75:	learn: 0.2176711	total: 1m 10s	remaining: 22.2s
76:	learn: 0.2174579	total: 1m 11s	remaining: 21.3s
77:	learn: 0.2172698	total: 1m 11s	remaining: 20.3s
78:	learn: 0.2170205	total: 1m 12s	remaining: 19.4s
79:	learn: 0.2167743	total: 1m 13s	remaining: 18.4s
80:	learn: 0.2165796	total: 1m 14s	remaining: 17.6s
81:	learn: 0.2162989	total: 

24:	learn: 0.2317317	total: 14.7s	remaining: 44.1s
25:	learn: 0.2313417	total: 15.3s	remaining: 43.4s
26:	learn: 0.2306153	total: 15.8s	remaining: 42.8s
27:	learn: 0.2303757	total: 16.2s	remaining: 41.8s
28:	learn: 0.2300681	total: 16.7s	remaining: 41s
29:	learn: 0.2298641	total: 17.2s	remaining: 40.2s
30:	learn: 0.2293537	total: 17.9s	remaining: 39.8s
31:	learn: 0.2291308	total: 18.3s	remaining: 38.9s
32:	learn: 0.2287221	total: 18.9s	remaining: 38.5s
33:	learn: 0.2283984	total: 19.4s	remaining: 37.7s
34:	learn: 0.2281464	total: 19.9s	remaining: 36.9s
35:	learn: 0.2277790	total: 20.4s	remaining: 36.3s
36:	learn: 0.2274380	total: 21s	remaining: 35.8s
37:	learn: 0.2271442	total: 21.6s	remaining: 35.2s
38:	learn: 0.2269899	total: 22.1s	remaining: 34.5s
39:	learn: 0.2267446	total: 22.6s	remaining: 33.8s
40:	learn: 0.2264329	total: 23.1s	remaining: 33.3s
41:	learn: 0.2260641	total: 23.7s	remaining: 32.7s
42:	learn: 0.2258720	total: 24.2s	remaining: 32.1s
43:	learn: 0.2256829	total: 24.7s	r

In [229]:
pro_ = bag.predict_proba(X_test)

In [230]:
pro_[:,1] = pro_[:,1]*3.0
pro_[:,2] = pro_[:,2]*2.9

In [231]:
pro_ = pro_/(pro_.sum(axis=1).reshape(-1,1))

In [232]:
pro_

array([[0.93145923, 0.04644406, 0.02209672],
       [0.95217656, 0.01846635, 0.02935709],
       [0.99319201, 0.00568014, 0.00112785],
       ...,
       [0.99289495, 0.00165172, 0.00545334],
       [0.97110148, 0.0220777 , 0.00682082],
       [0.92562842, 0.06998374, 0.00438784]])

In [233]:
y_test = np.argmax(pro_,axis=1)
y_test

array([0, 0, 0, ..., 0, 0, 0], dtype=int64)

In [234]:
len(np.where(y_test==0)[0])

169532

In [235]:
len(np.where(y_test==1)[0])

5097

In [236]:
len(np.where(y_test==2)[0])

1428

In [237]:
db = test[['link', 'current_slice_id', 'future_slice_id', 'label']]

In [238]:
db['label']=y_test+1

In [239]:
db.to_csv('2020-11-18-10.csv', index=False, encoding='utf8')

In [33]:
print(classification_report(y_train,y_train_pred, digits=4))
report = f1_score(y_train,y_train_pred, average=None)
print('Score: ', report[0] * 0.2 + report[1] * 0.2 + report[2] * 0.6)

              precision    recall  f1-score   support

           0     0.9209    0.9434    0.9320    415227
           1     0.6062    0.5338    0.5677     72621
           2     0.5199    0.4777    0.4979     18105

    accuracy                         0.8679    505953
   macro avg     0.6823    0.6516    0.6659    505953
weighted avg     0.8614    0.8679    0.8642    505953

Score:  0.5986666285495779


In [18]:
print(classification_report(y_ver,y_test_pred, digits=4))
report = f1_score(y_ver,y_test_pred, average=None)
print('Score: ', report[0] * 0.2 + report[1] * 0.2 + report[2] * 0.6)

              precision    recall  f1-score   support

           0     0.9309    0.9491    0.9399    416466
           1     0.6391    0.5791    0.6076     68946
           2     0.6363    0.5778    0.6056     18144

    accuracy                         0.8850    503556
   macro avg     0.7354    0.7020    0.7177    503556
weighted avg     0.8803    0.8850    0.8823    503556

Score:  0.6728864887095121


In [92]:
db = ver[[id_col, 'current_slice_id', 'future_slice_id', 'label']]

In [97]:
db.label = pred_res+1

In [98]:
db.to_csv('2020-11-10.csv', index=False, encoding='utf8')

In [58]:
415227/505953

0.8206829488114509